# Seoul

In [0]:
!pip install haversine
from haversine import haversine

In [0]:
from google.colab import drive
drive.mount('/content/gdrive')
mypath = r'/content/gdrive/My Drive/study/[coursera] IBM data science/data/'

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
import pandas as pd
import numpy as np
import os
import re
import json # library to handle JSON files
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe


import matplotlib.pyplot as plt
%matplotlib inline
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors


from bs4 import BeautifulSoup
import requests
import time
from tqdm import tqdm, trange
from pprint import pprint

# import k-means from clustering stage
from sklearn.cluster import KMeans
import folium # map rendering library

# Clustering the neighborhoods in Seoul
 - https://github.com/vuski/admdongkor

 - dong data: https://data.seoul.go.kr/dataList/OA-13221/S/1/datasetView.do

In [0]:
df_seoul = pd.read_csv(mypath + 'seoul_location.csv')
df_seoul_detail = pd.read_csv(mypath + 'seoul_location_detail.csv', usecols=['읍면동명', '읍면동영문명', '위도', '경도'])\
                             .rename(columns={'읍면동명': 'dong', '읍면동영문명': 'dong_eng', '위도': 'lat', '경도': 'lng'})
display(df_seoul.head())
display(df_seoul_detail.head())

district  district_eng        lat         lng
0      종로구     Jongno-gu  37.592128  126.979420
1       중구       Jung-gu  37.557335  126.997985
2      용산구    Yongsan-gu  37.528582  126.981987
3      성동구  Seongdong-gu  37.548240  127.043114
4      광진구   Gwangjin-gu  37.543059  127.088351

dong       dong_eng        lat         lng
0   가락동     Garak-dong  37.494280  127.117631
1  가리봉동  Garibong-dong  37.483017  126.887363
2   가산동     Gasan-dong  37.475469  126.884239
3   가양동    Gayang-dong  37.567984  126.844436
4   가회동     Gahoe-dong  37.582806  126.984865

In [0]:
# get every dong name of Seoul
result = list()
with open(mypath + 'seoul_geo.geojson', 'r') as f:
    for line in f.readlines():
        line_seg = line.split('\"')
        for component in line_seg:
            if '서울특별시' in component:
                result.append(component.split(' '))
df_naming = pd.DataFrame(result, columns=['si', 'gu', 'dong']).drop(columns='si')
df_naming

gu  dong
0    종로구   사직동
1    종로구   삼청동
2    종로구   부암동
3    종로구   평창동
4    종로구   무악동
..   ...   ...
419  강동구  둔촌1동
420  강동구  둔촌2동
421  강동구  암사1동
422  강동구  천호2동
423  강동구    길동

[424 rows x 2 columns]

In [0]:
def find_district(x):
    name = x[:-1]
    i = -1
    for index, dong in enumerate(df_naming['dong']):
        if name in dong:
            i = index
            break
    if i == -1:
        return None
    else:
        return df_naming['gu'].iloc[index]
df_seoul_detail['district'] = df_seoul_detail['dong'].apply(find_district)
df_seoul_detail = df_seoul_detail.loc[df_seoul_detail['district'].notnull()].reset_index(drop=True)

# data adjustment
dict_adjust = {'창동': '도봉구',
               '재동': '종로구',
               '계동': '종로구',
               '초동': '중구',
               '삼각동': '중구',
               '정동': '중구',
               '합동': '서대문구',
               '목동': '양천구',
               '본동': '동작구',
               '중동': '마포구',
               '항동': '구로구',
               }
for dong, gu in dict_adjust.items():
    df_seoul_detail.loc[df_seoul_detail['dong'] == dong, 'district'] = gu
df_seoul_detail

dong        dong_eng        lat         lng district
0     가락동      Garak-dong  37.494280  127.117631      송파구
1    가리봉동   Garibong-dong  37.483017  126.887363      구로구
2     가산동      Gasan-dong  37.475469  126.884239      금천구
3     가양동     Gayang-dong  37.567984  126.844436      강서구
4     가회동      Gahoe-dong  37.582806  126.984865      종로구
..    ...             ...        ...         ...      ...
193   효자동      Hyoja-dong  37.582704  126.971898      종로구
194   효창동   Hyochang-dong  37.543576  126.960722      용산구
195   후암동       Huam-dong  37.550385  126.980505      용산구
196   휘경동  Hwigyeong-dong  37.588185  127.064327     동대문구
197   흑석동   Heukseok-dong  37.505278  126.963823      동작구

[198 rows x 5 columns]

In [0]:
# Show seoul map

latitude = float(df_seoul.query('district_eng == "Jung-gu"')['lat'])
longitude = float(df_seoul.query('district_eng == "Jung-gu"')['lng'])
print(f'lat: {latitude}, lng: {longitude}')
# create map of seoul using latitude and longitude values
map_seoul = folium.Map(location=[latitude, longitude], zoom_start=12)


map_seoul.choropleth(
    geo_data=mypath + 'seoul_geo.geojson',
    columns=['Neighborhood', 'Count'],
    key_on='feature.properties.name',
#     fill_color='YlOrRd', 
    fill_color='royalblue',
    fill_opacity=0.2, 
    line_opacity=0.5,
)


for row in df_seoul.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    district = row.district

    label = '{}'.format(district)
    label = folium.Popup(label, parse_html=True)


    # folium.CircleMarker(
    #     [lat, lng],
    #     radius=5,
    #     popup=label,
    #     color='blue',
    #     fill=True,
    #     fill_color='#3186cc',
    #     fill_opacity=0.7,
    #     parse_html=False
    # ).add_to(map_seoul)  
    folium.Circle([lat, lng],
                  radius=2500).add_to(map_seoul)

map_seoul

lat: 37.557334999999995, lng: 126.99798500000001


/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [0]:
# Show seoul map - dong level

latitude = float(df_seoul.query('district_eng == "Jung-gu"')['lat'])
longitude = float(df_seoul.query('district_eng == "Jung-gu"')['lng'])
print(f'lat: {latitude}, lng: {longitude}')
# create map of seoul using latitude and longitude values
map_seoul_detail = folium.Map(location=[latitude, longitude], zoom_start=12)
map_seoul_detail.choropleth(
    geo_data=mypath + 'seoul_geo.geojson',
    columns=['Neighborhood', 'Count'],
    key_on='feature.properties.name',
#     fill_color='YlOrRd', 
    fill_color='royalblue',
    fill_opacity=0.2, 
    line_opacity=0.5,
)

for row in df_seoul_detail.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    district = row.district
    dong = row.dong

    label = '{}, {}'.format(district, dong)
    label = folium.Popup(label, parse_html=True)


    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False
    ).add_to(map_seoul_detail)  
    # folium.Circle([lat, lng],
    #               radius=1500).add_to(map_seoul_detail)

map_seoul_detail

lat: 37.557334999999995, lng: 126.99798500000001


/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [0]:
CLIENT_ID = 'xx' # your Foursquare ID
CLIENT_SECRET = 'yy' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 4BKPEWBN0OJAVWTUISLAPWWVRD25HF43PH5I33LTCWSD2DDW
CLIENT_SECRET:Z2ITUHJHIDGLM514RGPEKVZSQPWS4GTSAWWCPXLD0FXNPDCS


In [0]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [0]:
list_df = list()
for row in df_seoul_detail.itertuples(index=False):
    loc = row[0]
    loc_eng = row[1]
    lat = float(row[2])
    lng = float(row[3])

    LIMIT = 200 # limit of number of venues returned by Foursquare API
    radius = 1500 # define radius

    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'\
        .format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat,
            lng,
            radius, 
            LIMIT,
            )
        
    results = requests.get(url).json()
    print(results)
    venues = results['response']['groups'][0]['items']
    try:
        nearby_venues = json_normalize(venues) # flatten JSON
    

        # filter columns
        filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
        nearby_venues = nearby_venues.loc[:, filtered_columns]

    except:
        continue

    # filter the category for each row
    nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

    # clean columns
    nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

    nearby_venues['dong'] = loc
    
    list_df.append(nearby_venues)

df_seoul_venue = pd.concat(list_df).reset_index(drop=True)
df_seoul_venue

Output hidden; open in https://colab.research.google.com to view.

In [0]:
df_seoul_venue.drop_duplicates('name', inplace=True)
print('{} venues were returned by Foursquare.'.format(df_seoul_venue.shape[0]))

4707 venues were returned by Foursquare.


In [0]:
df_seoul_venue.categories.value_counts().head(30)

Korean Restaurant        643
Coffee Shop              285
Café                     270
BBQ Joint                217
Chinese Restaurant       180
Japanese Restaurant      152
Bakery                   137
Park                     136
Italian Restaurant       109
Noodle House             105
Hotel                    104
Seafood Restaurant        71
Sushi Restaurant          63
Dessert Shop              62
Trail                     59
Gym / Fitness Center      56
Fried Chicken Joint       51
Market                    44
Bus Stop                  42
Bunsik Restaurant         41
Historic Site             38
Sake Bar                  38
Vietnamese Restaurant     37
Multiplex                 35
Pizza Place               34
Bar                       33
Restaurant                32
Ice Cream Shop            30
Pub                       30
Burger Joint              30
Name: categories, dtype: int64

In [0]:
df_seoul_venue = df_seoul_venue.merge(df_seoul_detail[['dong', 'district']], on='dong')
df_seoul_venue

name         categories  ...  dong  district
0                   다농마트      Grocery Store  ...   가락동       송파구
1                함경도찹쌀순대  Korean Restaurant  ...   가락동       송파구
2                가락몰 회센터        Fish Market  ...   가락동       송파구
3                    오향가          BBQ Joint  ...   가락동       송파구
4                  횡성한우촌          BBQ Joint  ...   가락동       송파구
...                  ...                ...  ...   ...       ...
4799   ID 20-133 (국립현충원)           Bus Stop  ...   흑석동       동작구
4800            동작역앞 놀이터         Theme Park  ...   흑석동       동작구
4801  Dongjak Stn. (동작역)      Metro Station  ...   흑석동       동작구
4802           동작역 세븐일레븐  Convenience Store  ...   흑석동       동작구
4803     동작대교 남단 수상택시승강장      Boat or Ferry  ...   흑석동       동작구

[4804 rows x 6 columns]

In [0]:
df_seoul_venue

name         categories  ...  dong  district
0                   다농마트      Grocery Store  ...   가락동       송파구
1                함경도찹쌀순대  Korean Restaurant  ...   가락동       송파구
2                가락몰 회센터        Fish Market  ...   가락동       송파구
3                    오향가          BBQ Joint  ...   가락동       송파구
4                  횡성한우촌          BBQ Joint  ...   가락동       송파구
...                  ...                ...  ...   ...       ...
4799   ID 20-133 (국립현충원)           Bus Stop  ...   흑석동       동작구
4800            동작역앞 놀이터         Theme Park  ...   흑석동       동작구
4801  Dongjak Stn. (동작역)      Metro Station  ...   흑석동       동작구
4802           동작역 세븐일레븐  Convenience Store  ...   흑석동       동작구
4803     동작대교 남단 수상택시승강장      Boat or Ferry  ...   흑석동       동작구

[4804 rows x 6 columns]

# example - Jongno District

In [0]:
df_jongno = df_seoul_venue.query('district == "종로구"')
# df_jongno = df_seoul_venue
print(df_jongno.shape)df
df_jongno

(471, 6)


name          categories  ...  dong  district
188            GENTLE MONSTER (젠틀몬스터)        Optical Shop  ...   가회동       종로구
189    Bukchon Hanok Village (북촌한옥마을)             Village  ...   가회동       종로구
190   Baek In-Je House Museum (백인제가옥)       Historic Site  ...   가회동       종로구
191                     Terreno (떼레노)  Spanish Restaurant  ...   가회동       종로구
192       Cha Masineun Tteul (차마시는 뜰)            Tea Room  ...   가회동       종로구
...                               ...                 ...  ...   ...       ...
4725                             디마떼오         Pizza Place  ...   혜화동       종로구
4726         Arko Art Center (아르코미술관)         Art Gallery  ...   혜화동       종로구
4727                McDuck's Taphouse                 Pub  ...   혜화동       종로구
4728                            동숭동커피                Café  ...   혜화동       종로구
4729                    Tanosin (타노신)            Sake Bar  ...   혜화동       종로구

[471 rows x 6 columns]

In [0]:
df_jongno.categories.value_counts().to_frame().head(10)

categories
Korean Restaurant           56
Café                        36
Coffee Shop                 29
Historic Site               23
Italian Restaurant          14
Art Museum                  13
Chinese Restaurant          12
Bakery                      12
BBQ Joint                   12
Art Gallery                 12

In [0]:
# Show jongno map
init_latitude = float(df_jongno.iloc[0]['lat'])
init_longitude = float(df_jongno.iloc[0]['lng'])
# print(f'lat: {init_latitude}, lng: {init_longitude}')
# create map of jongno using latitude and longitude values
map_jongno = folium.Map(location=[latitude, longitude], zoom_start=13)
map_jongno.choropleth(
    geo_data=mypath + 'seoul_geo.geojson',
    columns=['Neighborhood', 'Count'],
    key_on='feature.properties.name',
#     fill_color='YlOrRd', 
    fill_color='royalblue',
    fill_opacity=0.2, 
    line_opacity=0.5,
)

like_cafe = ['Coffee Shop', 'Café', 'Bakery', 'Donut Shop', 'Dessert Shop', 'Bubble Tea Shop']
for row in df_jongno.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    district = row.district
    dong = row.dong
    
    label = '{}'.format(dong)
    label = folium.Popup(label, parse_html=True)

    if row.categories in like_cafe:
        circle_color = 'red'
    else:
        circle_color = 'royalblue'


    folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=circle_color,
        ).add_to(map_jongno)  
    # folium.Circle([lat, lng],
    #               radius=100,
    #               color=circle_color).add_to(map_jongno)

map_jongno

/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [0]:
df_jongno_dong = df_seoul_detail.query('district == "종로구"')
df_jongno_dong

dong          dong_eng        lat         lng district
4     가회동        Gahoe-dong  37.582806  126.984865      종로구
10     계동          Gye-dong  37.582904  126.986877      종로구
17    교남동       Gyonam-dong  37.568435  126.964474      종로구
57    무악동         Muak-dong  37.576791  126.958227      종로구
69    부암동         Buam-dong  37.593496  126.967285      종로구
75    사직동        Sajik-dong  37.575384  126.965826      종로구
79    삼청동    Samcheong-dong  37.589878  126.981380      종로구
101   숭인동       Sungin-dong  37.576675  127.019065      종로구
145   이화동         Ihwa-dong  37.577325  127.005471      종로구
153    재동          Jae-dong  37.578159  126.985253      종로구
158  종로1가   Jongno 1(il)-ga  37.570698  126.980334      종로구
159  종로5가    Jongno 5(o)-ga  37.570730  127.003350      종로구
169   창신동     Changsin-dong  37.576003  127.013525      종로구
174   청운동     Cheongun-dong  37.589029  126.968516      종로구
176    평동       Pyeong-dong  37.567673  126.966835      종로구
177   평창동  Pyeongchang-dong  37.613968  126.974302      종로구
185   혜화동       Hyehwa-dong  37.587822  127.002323      종로구
189    화동          Hwa-dong  37.580686  126.982610      종로구
193   효자동        Hyoja-dong  37.582704  126.971898      종로구

In [0]:
# Show jongno map
init_latitude = float(df_jongno.iloc[0]['lat'])
init_longitude = float(df_jongno.iloc[0]['lng'])
# print(f'lat: {init_latitude}, lng: {init_longitude}')
# create map of jongno using latitude and longitude values
map_jongno = folium.Map(location=[latitude, longitude], zoom_start=13)


for row in df_jongno_dong.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    dong = row.dong
    
    label = '{}'.format(dong)
    label = folium.Popup(label, parse_html=True)

    circle_color = 'black'
    folium.Circle([lat, lng],
                  radius=100,
                  color=circle_color).add_to(map_jongno)

map_jongno

# scoring

In [0]:
df_jongno

name          categories  ...  dong  district
188            GENTLE MONSTER (젠틀몬스터)        Optical Shop  ...   가회동       종로구
189    Bukchon Hanok Village (북촌한옥마을)             Village  ...   가회동       종로구
190   Baek In-Je House Museum (백인제가옥)       Historic Site  ...   가회동       종로구
191                     Terreno (떼레노)  Spanish Restaurant  ...   가회동       종로구
192       Cha Masineun Tteul (차마시는 뜰)            Tea Room  ...   가회동       종로구
...                               ...                 ...  ...   ...       ...
4725                             디마떼오         Pizza Place  ...   혜화동       종로구
4726         Arko Art Center (아르코미술관)         Art Gallery  ...   혜화동       종로구
4727                McDuck's Taphouse                 Pub  ...   혜화동       종로구
4728                            동숭동커피                Café  ...   혜화동       종로구
4729                    Tanosin (타노신)            Sake Bar  ...   혜화동       종로구

[471 rows x 6 columns]

In [0]:
df_jongno_cafe = df_jongno.query('categories in @like_cafe')
df_jongno_non_cafe = df_jongno.query('categories not in @like_cafe')
df_jongno_cafe

name    categories  ...  dong  district
193             CAFE ROSSO (로쏘)          Café  ...   가회동       종로구
195         Cafe dooroo (카페 두루)          Café  ...   가회동       종로구
196         Cafe Gondry (카페공드리)          Café  ...   가회동       종로구
198            Cafe yido (카페이도)          Café  ...   가회동       종로구
202   Blue Bottle Coffee (블루보틀)   Coffee Shop  ...   가회동       종로구
...                         ...           ...  ...   ...       ...
4656     sueño339+cafe (수애뇨339)          Café  ...   평창동       종로구
4663           Sky Cafe (스카이카페)   Coffee Shop  ...   평창동       종로구
4718                  b2project          Café  ...   혜화동       종로구
4724              Cafe The Snow  Dessert Shop  ...   혜화동       종로구
4728                      동숭동커피          Café  ...   혜화동       종로구

[86 rows x 6 columns]

In [0]:
def cafe_count(x):
    lat = x['lat']
    lng = x['lng']

    cafe_count = 0
    for row in df_jongno_cafe.itertuples(index=False):
        cafe_lat = row.lat
        cafe_lng = row.lng
        if haversine([lat, lng], [cafe_lat, cafe_lng]) < 1:
            cafe_count += 1

    non_cafe_count = 0
    for row in df_jongno_non_cafe.itertuples(index=False):
        non_cafe_lat = row.lat
        non_cafe_lng = row.lng
        if haversine([lat, lng], [non_cafe_lat, non_cafe_lng]) < 1:
            non_cafe_count += 1
    
    return pd.Series([cafe_count, non_cafe_count])
df_jongno_dong[['cafe_count', 'non_cafe_count']] = df_jongno_dong.apply(cafe_count, axis=1)

/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:3509: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [0]:
df_jongno_dong

dong          dong_eng        lat  ...  district cafe_count  non_cafe_count
4     가회동        Gahoe-dong  37.582806  ...       종로구         19              72
10     계동          Gye-dong  37.582904  ...       종로구         19              73
17    교남동       Gyonam-dong  37.568435  ...       종로구          8              54
57    무악동         Muak-dong  37.576791  ...       종로구          4              16
69    부암동         Buam-dong  37.593496  ...       종로구          4              19
75    사직동        Sajik-dong  37.575384  ...       종로구         24              77
79    삼청동    Samcheong-dong  37.589878  ...       종로구          8              33
101   숭인동       Sungin-dong  37.576675  ...       종로구          2              10
145   이화동         Ihwa-dong  37.577325  ...       종로구          7              64
153    재동          Jae-dong  37.578159  ...       종로구         24              82
158  종로1가   Jongno 1(il)-ga  37.570698  ...       종로구         19             108
159  종로5가    Jongno 5(o)-ga  37.570730  ...       종로구          6              61
169   창신동     Changsin-dong  37.576003  ...       종로구          5              34
174   청운동     Cheongun-dong  37.589029  ...       종로구         12              28
176    평동       Pyeong-dong  37.567673  ...       종로구          8              63
177   평창동  Pyeongchang-dong  37.613968  ...       종로구          8              18
185   혜화동       Hyehwa-dong  37.587822  ...       종로구          6              31
189    화동          Hwa-dong  37.580686  ...       종로구         24              94
193   효자동        Hyoja-dong  37.582704  ...       종로구         28              86

[19 rows x 7 columns]

In [0]:
df_jongno_dong['score'] = df_jongno_dong['non_cafe_count'] - df_jongno_dong['cafe_count']
df_jongno_dong.sort_values('score', ascending=False)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


dong          dong_eng        lat  ...  cafe_count non_cafe_count  score
158  종로1가   Jongno 1(il)-ga  37.570698  ...          19            108     89
189    화동          Hwa-dong  37.580686  ...          24             94     70
153    재동          Jae-dong  37.578159  ...          24             82     58
193   효자동        Hyoja-dong  37.582704  ...          28             86     58
145   이화동         Ihwa-dong  37.577325  ...           7             64     57
159  종로5가    Jongno 5(o)-ga  37.570730  ...           6             61     55
176    평동       Pyeong-dong  37.567673  ...           8             63     55
10     계동          Gye-dong  37.582904  ...          19             73     54
75    사직동        Sajik-dong  37.575384  ...          24             77     53
4     가회동        Gahoe-dong  37.582806  ...          19             72     53
17    교남동       Gyonam-dong  37.568435  ...           8             54     46
169   창신동     Changsin-dong  37.576003  ...           5             34     29
79    삼청동    Samcheong-dong  37.589878  ...           8             33     25
185   혜화동       Hyehwa-dong  37.587822  ...           6             31     25
174   청운동     Cheongun-dong  37.589029  ...          12             28     16
69    부암동         Buam-dong  37.593496  ...           4             19     15
57    무악동         Muak-dong  37.576791  ...           4             16     12
177   평창동  Pyeongchang-dong  37.613968  ...           8             18     10
101   숭인동       Sungin-dong  37.576675  ...           2             10      8

[19 rows x 8 columns]

In [0]:
# Show jongno map
init_latitude = float(df_jongno.iloc[0]['lat'])
init_longitude = float(df_jongno.iloc[0]['lng'])
# print(f'lat: {init_latitude}, lng: {init_longitude}')
# create map of jongno using latitude and longitude values
map_jongno = folium.Map(location=[latitude, longitude], zoom_start=13)
map_jongno.choropleth(
    geo_data=mypath + 'jongno-gu.geojson',
    columns=['Neighborhood', 'Count'],
    key_on='feature.properties.name',
#     fill_color='YlOrRd', 
    fill_color='royalblue',
    fill_opacity=0.2, 
    line_opacity=0.5,
)

like_cafe = ['Coffee Shop', 'Café', 'Bakery', 'Donut Shop', 'Dessert Shop', 'Bubble Tea Shop']
for row in df_jongno.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    district = row.district
    dong = row.dong
    
    label = '{}'.format(dong)
    label = folium.Popup(label, parse_html=True)

    if row.categories in like_cafe:
        circle_color = 'red'
    else:
        circle_color = 'royalblue'


    folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=circle_color,
        ).add_to(map_jongno) 

for row in df_jongno_dong.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    dong = row.dong
    
    label = '{}'.format(dong)
    label = folium.Popup(label, parse_html=True)

    if dong == "종로1가":
        circle_color = 'blue'
    elif dong == "숭인동":
        circle_color = 'red'
    else:
        continue
    folium.Circle([lat, lng],
                  radius=1000,
                  color=circle_color).add_to(map_jongno)

map_jongno

/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


# all district

In [0]:
def cafe_count(x, cafe, non_cafe):
    lat = x['lat']
    lng = x['lng']

    cafe_count = 0
    for row in cafe.itertuples(index=False):
        cafe_lat = row.lat
        cafe_lng = row.lng
        if haversine([lat, lng], [cafe_lat, cafe_lng]) < 1:
            cafe_count += 1

    non_cafe_count = 0
    for row in non_cafe.itertuples(index=False):
        non_cafe_lat = row.lat
        non_cafe_lng = row.lng
        if haversine([lat, lng], [non_cafe_lat, non_cafe_lng]) < 1:
            non_cafe_count += 1
    
    return pd.Series([cafe_count, non_cafe_count])
    
        
# variable define
like_cafe = ['Coffee Shop', 'Café', 'Bakery', 'Donut Shop', 'Dessert Shop', 'Bubble Tea Shop']
list_district = df_seoul['district']
list_result = list()

for district in list_district:
    # each district
    df_district = df_seoul_venue.loc[df_seoul_venue['district'] == district]

    # split cafe / non_cafe
    df_district_cafe = df_district.query('categories in @like_cafe')
    df_district_non_cafe = df_district.query('categories not in @like_cafe')

    # "dong" level information
    df_district_dong = df_seoul_detail.loc[df_seoul_detail['district'] == district]

    # count calculation
    df_district_dong[['cafe_count', 'non_cafe_count']] = df_district_dong.apply(lambda x: cafe_count(x, df_district_cafe, df_district_non_cafe), axis=1)

    # scoring each "dong"
    df_district_dong['score'] = df_district_dong['non_cafe_count'] - df_district_dong['cafe_count']
    list_result.append(df_district_dong)

df_result = pd.concat(list_result)

/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:3509: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [0]:
df_result.sort_values('score', ascending=False)

dong         dong_eng        lat  ...  cafe_count non_cafe_count  score
158  종로1가  Jongno 1(il)-ga  37.570698  ...          19            108     89
144  이태원동     Itaewon-dong  37.538862  ...          23            107     84
86    서교동      Seogyo-dong  37.553650  ...          42            120     78
95    소공동      Sogong-dong  37.563898  ...          13             91     78
33     다동          Da-dong  37.567883  ...          15             90     75
..    ...              ...        ...  ...         ...            ...    ...
96    송정동   Songjeong-dong  37.554104  ...           2              2      0
103   신길동      Singil-dong  37.505826  ...           1              1      0
102   시흥동     Siheung-dong  37.449703  ...           1              1      0
139   월계동      Wolgye-dong  37.629556  ...           1              1      0
167   진관동     Jingwan-dong  37.642252  ...           6              5     -1

[198 rows x 8 columns]

In [0]:
df_seoul_detail

dong        dong_eng        lat         lng district
0     가락동      Garak-dong  37.494280  127.117631      송파구
1    가리봉동   Garibong-dong  37.483017  126.887363      구로구
2     가산동      Gasan-dong  37.475469  126.884239      금천구
3     가양동     Gayang-dong  37.567984  126.844436      강서구
4     가회동      Gahoe-dong  37.582806  126.984865      종로구
..    ...             ...        ...         ...      ...
193   효자동      Hyoja-dong  37.582704  126.971898      종로구
194   효창동   Hyochang-dong  37.543576  126.960722      용산구
195   후암동       Huam-dong  37.550385  126.980505      용산구
196   휘경동  Hwigyeong-dong  37.588185  127.064327     동대문구
197   흑석동   Heukseok-dong  37.505278  126.963823      동작구

[198 rows x 5 columns]

# result check

In [0]:
# Show jongno map
init_latitude = float(df_jongno.iloc[0]['lat'])
init_longitude = float(df_jongno.iloc[0]['lng'])
# print(f'lat: {init_latitude}, lng: {init_longitude}')
# create map of jongno using latitude and longitude values
map_jongno = folium.Map(location=[latitude, longitude], zoom_start=13)
map_jongno.choropleth(
    geo_data=mypath + 'seoul_geo.geojson',
    columns=['Neighborhood', 'Count'],
    key_on='feature.properties.name',
#     fill_color='YlOrRd', 
    fill_color='royalblue',
    fill_opacity=0.2, 
    line_opacity=0.5,
)

like_cafe = ['Coffee Shop', 'Café', 'Bakery', 'Donut Shop', 'Dessert Shop', 'Bubble Tea Shop']
df_temp = df_seoul_venue.sample(1000)
for row in df_temp.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    district = row.district
    dong = row.dong
    
    label = '{}'.format(dong)
    label = folium.Popup(label, parse_html=True)

    if row.categories in like_cafe:
        circle_color = 'red'
    else:
        circle_color = 'royalblue'


    # folium.CircleMarker(
    #         [lat, lng],
    #         radius=5,
    #         popup=label,
    #         color=circle_color,
    #     ).add_to(map_jongno)  
    folium.Circle([lat, lng],
                  radius=100,
                  color=circle_color).add_to(map_jongno)


for row in df_seoul_detail.itertuples(index=False):
    lat = row.lat
    lng = row.lng
    dong = row.dong
    
    label = '{}'.format(dong)
    label = folium.Popup(label, parse_html=True)

    best_place = ['종로1가', '이태원동', '서교동', '소공동', '다동']
    worst_place = ['송정동', '신길동', '시흥동', '월계동', '진관동']
    if dong in best_place:
        circle_color = 'blue'
    elif dong in worst_place:
        circle_color = 'red'
    else:
        continue
    folium.Circle([lat, lng],
                  radius=1000,
                  color=circle_color).add_to(map_jongno)
map_jongno

/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
